In [2]:
import pandas as pd
import mysql.connector
import plotly.express as px
from dotenv import load_dotenv
import os

In [3]:
load_dotenv()
DB_PW = os.getenv('DB_PW')

# Connect to the database
connection = mysql.connector.connect(
    host='localhost',
    user='root',
    password=DB_PW,
    database='hospital_register'
)

# Create a cursor object
cursor = connection.cursor()

In [4]:
from sqlalchemy import create_engine
import pandas as pd

load_dotenv()
DB_PW = os.getenv('DB_PW')


# Database connection parameters
username = 'root'
password = DB_PW
host = 'localhost'
port = '3306'
database = 'hospital_register'

# Create SQLAlchemy engine
engine = create_engine(f'mysql+pymysql://{username}:{password}@{host}:{port}/{database}')

query = """
    SELECT name, beds_number, latitude, longitude
    FROM hospital_locations
    """

# Read data from SQL database into a DataFrame
df_hospitals = pd.read_sql(query, engine)

In [8]:
df_hospitals

name  beds_number  \
0                             Klinikum Südstadt Rostock          539   
1     Harzklinikum Dorothea Christiane Erxleben GmbH...          320   
2     Harzklinikum Dorothea Christiane Erxleben GmbH...          300   
3      Sana Kliniken Leipziger Land GmbH Klinik Zwenkau           59   
4      Sana Kliniken Leipziger Land GmbH Klinikum Borna          508   
...                                                 ...          ...   
1653                          Medic-Center Klinik Fürth            6   
1654     Benedictus Krankenhaus Feldafing GmbH & Co. KG          100   
1655              Sana Kliniken Landkreis Biberach GmbH          379   
1656                     RoMed Klinik Wasserburg a. Inn           12   
1657      Algesiologikum Tagesklinik für Schmerzmedizin            0   

       latitude  longitude  
0     54.071751  12.107268  
1     51.795329  11.163533  
2     51.835429  10.774409  
3     51.220290  12.330017  
4     51.134329  12.504938  
...         ...        ...  
1653  49.484538  10.974974  
1654  47.937803  11.294115  
1655  48.111633   9.779115  
1656  48.060546  12.198262  
1657  48.151827  11.620465  

[1658 rows x 4 columns]

In [4]:
df_places = pd.read_csv('../data/in/staging/atlas_places.csv')
df_places = df_places[['city', 'latitude', 'longitude']]#.drop_duplicates(subset=['city'])
df_places

city  latitude  longitude
0          Flensburg  54.78643    9.43339
1          Flensburg  54.78643    9.43339
2          Flensburg  54.79203    9.47724
3          Flensburg  54.77985    9.41820
4          Flensburg  54.77985    9.41820
...              ...       ...        ...
81944  Windischleuba  51.00745   12.50337
81945  Windischleuba  51.00356   12.47453
81946  Windischleuba  50.99752   12.47565
81947  Windischleuba  51.01629   12.46924
81948  Windischleuba  51.02705   12.45651

[81949 rows x 3 columns]

In [5]:
import numpy as np

def haversine(lat1, lon1, lat2, lon2):
    """
    Calculate the distance between two sets of latitude and longitude coordinates using the Haversine formula.
    """
    # Convert latitude and longitude to radians
    lat1_rad = np.radians(lat1)
    lon1_rad = np.radians(lon1)
    lat2_rad = np.radians(lat2)
    lon2_rad = np.radians(lon2)

    # Calculate the differences between the coordinates
    dlat = lat2_rad - lat1_rad
    dlon = lon2_rad - lon1_rad

    # Apply the Haversine formula
    a = np.sin(dlat / 2) ** 2 + np.cos(lat1_rad) * np.cos(lat2_rad) * np.sin(dlon / 2) ** 2
    c = 2 * np.arcsin(np.sqrt(a))
    r = 6371  # Radius of the Earth in kilometers

    # Calculate the distance
    distance = c * r

    return distance

# Calculate the distance to the nearest place in df_hospitals for each row in df_places
df_places['nearest_distance'] = df_places.apply(lambda row: np.min(haversine(row['latitude'], row['longitude'], df_hospitals['latitude'], df_hospitals['longitude'])), axis=1)

df_places

city  latitude  longitude  nearest_distance
0          Flensburg  54.78643    9.43339          0.383266
1          Flensburg  54.78643    9.43339          0.383266
2          Flensburg  54.79203    9.47724          3.252288
3          Flensburg  54.77985    9.41820          0.949793
4          Flensburg  54.77985    9.41820          0.949793
...              ...       ...        ...               ...
81944  Windischleuba  51.00745   12.50337          5.976773
81945  Windischleuba  51.00356   12.47453          4.305552
81946  Windischleuba  50.99752   12.47565          3.822888
81947  Windischleuba  51.01629   12.46924          5.376849
81948  Windischleuba  51.02705   12.45651          6.270596

[81949 rows x 4 columns]

In [6]:
#df_places.to_csv('../data/in/staging/atlas_places_with_distance.csv', index=False)
df_places = pd.read_csv('../data/in/staging/atlas_places_with_distance.csv')

In [20]:
import plotly.graph_objects as go

# Normalize the marker sizes
min_size = 5
max_size = 20
normalized_sizes = (df_hospitals['beds_number'] - df_hospitals['beds_number'].min()) / (df_hospitals['beds_number'].max() - df_hospitals['beds_number'].min()) * (max_size - min_size) + min_size

# Create the first layer
first_layer = go.Scattermapbox(
    lat=df_places['latitude'],
    lon=df_places['longitude'],
    mode='markers',
    marker=go.scattermapbox.Marker(
        size=10,  # Fixed size for the first layer markers
        color=df_places['nearest_distance'],  # Column for color scale
        colorscale='OrRd',  # Specify the color scale
        colorbar=dict(
            title=dict(text="Place [distance to nearest hospital]", side="top"),
            orientation='h',  # Horizontal orientation
            x=0.5,  # Center horizontally
            y=-0.15  # Position below the plot
        )
    ),
    text=df_places['city'],  # Hover text
    hoverinfo='text',
    showlegend=False
)

# Create the second layer with a color scale and scaled marker sizes
second_layer = go.Scattermapbox(
    lat=df_hospitals['latitude'],
    lon=df_hospitals['longitude'],
    mode='markers',
    marker=go.scattermapbox.Marker(
        size=normalized_sizes,  # Scaled size of the markers
        color=df_hospitals['beds_number'],  # Column for color scale
        colorscale='Blugrn',  # Specify the color scale
        colorbar=dict(
            title=dict(text="Hospital [number of beds]", side="top"),
            orientation='h',  # Horizontal orientation
            x=0.5,  # Center horizontally
            y=-0.25  # Position below the first colorbar
        )
    ),
    text=df_hospitals['name'],  # Hover text
    hoverinfo='text',
    showlegend=False
)

# Create the figure and add both layers
fig = go.Figure()

fig.add_trace(first_layer)
fig.add_trace(second_layer)

# Update the layout
fig.update_layout(
    mapbox=dict(
        style="carto-positron",  # Map style
        center=dict(lat=51.2, lon=10.5),  # Center of the map
        zoom=5  # Initial zoom level
    ),
    width=800,  # Set width in pixels
    height=1000  # Set height in pixels
)

fig.show()

In [ ]:
# Create a density map
fig = px.density_mapbox(
    df, 
    lat='latitude', 
    lon='longitude', 
    z='beds_number',  # The column representing the value you want to visualize
    radius=15,  # Radius of each point (can be adjusted)
    center=dict(lat=51, lon=10),  # Center of the map
    zoom=5,  # Initial zoom level
    mapbox_style="carto-positron",  # dark-mode: "carto-darkmatter", etc.
    color_continuous_scale=px.colors.sequential.Plasma
)

# Update figure size
fig.update_layout(
    width=800,  # Set width in pixels
    height=800  # Set height in pixels
)

fig.show()

In [ ]:
fig = px.scatter_mapbox(
    df, 
    lat='latitude', 
    lon='longitude', 
    #color='beds_number',  # The column representing the value you want to visualize
    size='beds_number',  # Optional: size of points based on value
    color_continuous_scale=px.colors.cyclical.IceFire,  # Customize color scale
    size_max=15,  # Maximum size of points
    zoom=5,  # Initial zoom level
    mapbox_style="carto-darkmatter"  # You can use other styles
)

# Update figure size
fig.update_layout(
    width=800,  # Set width in pixels
    height=800  # Set height in pixels
)

fig.show()

In [ ]:
import plotly.graph_objects as go
import pandas as pd

polygon_coords = [
    {"lat": 37.78, "lon": -122.42},
    {"lat": 37.79, "lon": -122.41},
    {"lat": 37.78, "lon": -122.40},
    {"lat": 37.77, "lon": -122.41},
    {"lat": 37.78, "lon": -122.42}  # Close the polygon by repeating the first point
]

fig = go.Figure()

# Add the polygon to the map
fig.add_trace(go.Scattermapbox(
    fill="toself",  # Fill the area inside the polygon
    lon=[point['lon'] for point in polygon_coords],
    lat=[point['lat'] for point in polygon_coords],
    marker={'size': 0, 'color': "red"},  # You can change the color here
    name="Shaded Area"
))

# Set up the layout for the Mapbox
fig.update_layout(
    mapbox=dict(
        style="open-street-map",
        center={"lat": 37.78, "lon": -122.42},
        zoom=12
    ),
    showlegend=True
)

fig.show()
